In [1]:
import os
# set GPU number. This might work for several framework such as PyTorch, TensorFlow, Keras
gpu_id = '0'
os.environ["CUDA_VISIBLE_DEVICES"]=gpu_id

In [2]:
import warnings
warnings.filterwarnings("ignore")

In [3]:
# sys.path.append('../../loglizer')
    
# from loglizer import dataloader
# from loglizer.preprocessing import Vectorizer, Iterator
import sys
import torch
import torch.nn as nn
import torch.nn.functional as func
import torch.optim as optim
from torch.utils.data import Dataset
import torch.utils.data as Data
import pickle as pkl
import argparse
import time
import copy
import torchvision.transforms as transforms
import torchvision
import random
from collections import OrderedDict
from PIL import Image

import pandas as pd
import math
import matplotlib.pyplot as plt
import numpy as np

from sklearn.metrics import accuracy_score, f1_score, recall_score, precision_score
from collections import defaultdict

In [4]:
# struct_log = '../data/HDFS/HDFS.log_structured.csv' # The structured log file

#初始參數
class Parser():
    def __init__(self):
        self.mode = 'fedavg'  #FedBN,FedAvg,fedprox,fedopt,fedadagrad,fedadam 待加入scoffold
        #所有方法都有使用Fedbn
        self.beta_1 = 0.9
        self.beta_2 = 0.99 #b1,b2 for adaptive opt
        self.tau = 1e-2
        self.batch = 32
        self.lr = 1e-2
        self.server_lr = 1e-3
        self.server_momentum = 0.5
        self.client_momentum = 0.9 # 0 is fedavg others is fedavgm
        self.no_cuda = False
        self.seed = 1
        self.client_num = 5
        self.wk_iters = 1 # training
        self.num_workers = 2 # dataloader
        self.mu = 1e-3
        self.iters = 500 #epochs
        self.local_epoches = 1
        self.server_opt = 'sgd'
        self.percent = 1
#         self.early_stop = 500
        self.window_size = 10
        self.train_ratio = 0.5
        self.split_type='sequential' # sequential, uniform

        
args = Parser()

use_cuda = not args.no_cuda and torch.cuda.is_available()
np.random.seed(args.seed)
torch.manual_seed(args.seed)
torch.cuda.manual_seed_all(args.seed) 
random.seed(args.seed)
device = torch.device("cuda" if use_cuda else "cpu")

In [5]:
sys.path.append('../')
from logdeep.models.lstm import deeplog, loganomaly, robustlog
from logdeep.tools.predict import Predicter
from logdeep.tools.train import Trainer
from logdeep.tools.utils import *

# Config Parameters

options = dict()
options['data_dir'] = '../data/'
options['window_size'] = 10
options['device'] = 0

# Smaple
options['sample'] = "sliding_window"
options['window_size'] = 10  # if fix_window

# Features
options['sequentials'] = True
options['quantitatives'] = False
options['semantics'] = False
options['feature_num'] = sum(
    [options['sequentials'], options['quantitatives'], options['semantics']])

# Model
options['input_size'] = 1
options['hidden_size'] = 64
options['num_layers'] = 2
options['num_classes'] = 28

# Train
options['batch_size'] = 2048
options['accumulation_step'] = 1

options['optimizer'] = 'adam'
options['lr'] = 0.001
options['max_epoch'] = 1
options['lr_step'] = (300, 350)
options['lr_decay_ratio'] = 0.1

options['resume_path'] = None
options['model_name'] = "deeplog"
options['save_dir'] = "../result/deeplog/"

# Predict
options['model_path'] = "../result/deeplog/deeplog_last.pth"
options['num_candidates'] = 9

seed_everything(seed=1234)


def train():
    trainer = Trainer(Model, options)
    trainer.start_train()


def predict():
    predicter = Predicter(Model, options)
    predicter.predict_unsupervised()

# Preprocessing

In [6]:
# df = pd.read_csv(struct_log)
# print(df.shape)

# for i in range(args.client_num):
#     bound = int(df.shape[0]/args.client_num)
#     ddf = df[i* bound : (i+1)* bound]
#     ddf.to_csv("../../loglizer/data/client_alldata/client_"+str(i)+".csv", index=None)
#     print('Client',i, ddf.shape)
#     del ddf
# del df 

In [7]:
class deeplog(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, num_keys):
        super(deeplog, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.lstm = nn.LSTM(input_size,
                            hidden_size,
                            num_layers,
                            batch_first=True)
        self.fc = nn.Linear(hidden_size, num_keys)

    def forward(self, features, device):
        input0 = features[0]
        h0 = torch.zeros(self.num_layers, input0.size(0),
                         self.hidden_size).to(device)
        c0 = torch.zeros(self.num_layers, input0.size(0),
                         self.hidden_size).to(device)
        out, _ = self.lstm(input0, (h0, c0))
        out = self.fc(out[:, -1, :])
        return out


class loganomaly(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, num_keys):
        super(loganomaly, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.lstm0 = nn.LSTM(input_size,
                             hidden_size,
                             num_layers,
                             batch_first=True)
        self.lstm1 = nn.LSTM(input_size,
                             hidden_size,
                             num_layers,
                             batch_first=True)
        self.fc = nn.Linear(2 * hidden_size, num_keys)
        self.attention_size = self.hidden_size

        self.w_omega = Variable(
            torch.zeros(self.hidden_size, self.attention_size))
        self.u_omega = Variable(torch.zeros(self.attention_size))

        self.sequence_length = 28

    def attention_net(self, lstm_output):
        output_reshape = torch.Tensor.reshape(lstm_output,
                                              [-1, self.hidden_size])
        attn_tanh = torch.tanh(torch.mm(output_reshape, self.w_omega))
        attn_hidden_layer = torch.mm(
            attn_tanh, torch.Tensor.reshape(self.u_omega, [-1, 1]))
        exps = torch.Tensor.reshape(torch.exp(attn_hidden_layer),
                                    [-1, self.sequence_length])
        alphas = exps / torch.Tensor.reshape(torch.sum(exps, 1), [-1, 1])
        alphas_reshape = torch.Tensor.reshape(alphas,
                                              [-1, self.sequence_length, 1])
        state = lstm_output
        attn_output = torch.sum(state * alphas_reshape, 1)
        return attn_output

    def forward(self, features, device):
        input0, input1 = features[0], features[1]

        h0_0 = torch.zeros(self.num_layers, input0.size(0),
                           self.hidden_size).to(device)
        c0_0 = torch.zeros(self.num_layers, input0.size(0),
                           self.hidden_size).to(device)

        out0, _ = self.lstm0(input0, (h0_0, c0_0))

        h0_1 = torch.zeros(self.num_layers, input1.size(0),
                           self.hidden_size).to(device)
        c0_1 = torch.zeros(self.num_layers, input1.size(0),
                           self.hidden_size).to(device)

        out1, _ = self.lstm1(input1, (h0_1, c0_1))
        multi_out = torch.cat((out0[:, -1, :], out1[:, -1, :]), -1)
        out = self.fc(multi_out)
        return out


class robustlog(nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, num_keys):
        super(robustlog, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.lstm = nn.LSTM(input_size,
                            hidden_size,
                            num_layers,
                            batch_first=True)
        self.fc = nn.Linear(hidden_size, num_keys)

    def forward(self, features, device):
        input0 = features[0]
        h0 = torch.zeros(self.num_layers, input0.size(0),
                         self.hidden_size).to(device)
        c0 = torch.zeros(self.num_layers, input0.size(0),
                         self.hidden_size).to(device)
        out, _ = self.lstm(input0, (h0, c0))
        out = self.fc(out[:, -1, :])
        return out


In [8]:
# def datasplit(args, gpu_id = 1):
#     train_loaders = []
#     test_loaders = []
#     hidden_size = 32
#     num_directions = 2
#     topk = 5
    
#     for i in range(args.client_num):
#         struct_log = '../../loglizer/data/client_data/client_'+str(i)+".csv"
#         label_file = '../../loglizer/data/HDFS/anomaly_label.csv' # The anomaly label file
        
#         (x_train, window_y_train, y_train), (x_test, window_y_test, y_test) = dataloader.load_HDFS(i, struct_log, label_file = label_file, window='session', window_size=args.window_size, train_ratio=args.train_ratio, split_type=args.split_type)
#         feature_extractor = Vectorizer()
#         train_dataset = feature_extractor.fit_transform(x_train, window_y_train, y_train)
#         test_dataset = feature_extractor.transform(x_test, window_y_test, y_test)
#         train_loader = Iterator(train_dataset, batch_size=args.batch, shuffle=True, num_workers=args.num_workers).iter
#         test_loader = Iterator(test_dataset, batch_size=args.batch, shuffle=False, num_workers=args.num_workers).iter
#         train_loaders.append(train_loader)
#         test_loaders.append(test_loader)
        
#     server_model = DeepLog(num_labels=feature_extractor.num_labels, hidden_size=hidden_size, num_directions=num_directions, topk=topk).to(device)
    
#     return train_loaders, test_loaders, server_model

In [9]:
# train_loaders, test_loaders, server_model = datasplit(args, gpu_id = 1)

# Federated learning

In [10]:
def communication(args, server_model, models, client_weights, v, grad):
    if args.mode.lower() == 'fedbn':
        with torch.no_grad():
            for key in server_model.state_dict().keys():
                if 'bn' not in key: #非BN層都去交換
                    temp = torch.zeros_like(server_model.state_dict()[key], dtype=torch.float32)
                    for client_idx in range(client_num):
                        temp += client_weights[client_idx] * models[client_idx].state_dict()[key]
                    server_model.state_dict()[key].data.copy_(temp)
                    for client_idx in range(client_num):
                        models[client_idx].state_dict()[key].data.copy_(server_model.state_dict()[key])
    
    elif args.mode.lower() == 'fedadagrad':
        with torch.no_grad():
            for key, param in server_model.named_parameters():
                temp = torch.zeros_like(server_model.state_dict()[key])
                for client_idx in range(len(client_weights)):
                    temp = temp + client_weights[client_idx] * models[client_idx].state_dict()[key]                          
                param.grad = temp - param.data              
                param.grad = torch.mul(grad[key], args.beta_1) + torch.mul(param.grad, 1-args.beta_1)
                grad[key] = param.grad
                v[key] = v[key] + param.grad**2
                param.data = param.data + torch.mul(torch.div(param.grad, torch.add(torch.sqrt(v[key]),args.tau)), args.server_lr) 

                for client_idx in range(len(client_weights)):
                    models[client_idx].state_dict()[key].data.copy_(server_model.state_dict()[key])            
    
    elif args.mode.lower() == 'fedadam':
        with torch.no_grad():
            for key, param in server_model.named_parameters():                
                temp = torch.zeros_like(server_model.state_dict()[key])
                for client_idx in range(len(client_weights)):
                    temp += client_weights[client_idx] * models[client_idx].state_dict()[key]                         
                param.grad = temp - param.data              
                param.grad = torch.mul(grad[key], args.beta_1) + torch.mul(param.grad, 1-args.beta_1) 
                grad[key] = param.grad                
                v[key] = torch.mul(v[key], args.beta_2) + torch.mul(param.grad**2, 1-args.beta_2)
                param.data = param.data + torch.mul(torch.div(param.grad, torch.add(torch.sqrt(v[key]),args.tau)), args.server_lr)
                
                for client_idx in range(len(client_weights)):
                    models[client_idx].state_dict()[key].data.copy_(server_model.state_dict()[key])

    else:
        with torch.no_grad():
            for key in server_model.state_dict().keys():#遇到BN層就直接拿第一個client參數使用
                # num_batches_tracked is a non trainable LongTensor and
                # num_batches_tracked are the same for all clients for the given datasets
                if 'num_batches_tracked' in key:
                    server_model.state_dict()[key].data.copy_(models[0].state_dict()[key])
                else:
                    temp = torch.zeros_like(server_model.state_dict()[key]).to(device)
                    for client_idx in range(len(client_weights)):
                        temp += client_weights[client_idx] * models[client_idx].state_dict()[key]                        
                    server_model.state_dict()[key].data.copy_(temp)#weight傳給server
                    for client_idx in range(len(client_weights)):
                        models[client_idx].state_dict()[key].data.copy_(server_model.state_dict()[key])        
    return server_model, models, v, grad

In [11]:
# # setup model
server_model = deeplog(input_size=options['input_size'],
                    hidden_size=options['hidden_size'],
                    num_layers=options['num_layers'],
                    num_keys=options['num_classes'])
# for adaptive velocity
v = {}
grad = {}
for key in server_model.state_dict().keys():
    v[key] = torch.add(torch.zeros_like(server_model.state_dict()[key],dtype=torch.float32),args.tau**2)
    grad[key] = torch.zeros_like(server_model.state_dict()[key],dtype=torch.float32)
loss_fun = nn.CrossEntropyLoss()
# name of each datasets
datasets = ['Client'+str(i) for i in range(args.client_num)]
# federated client number
client_num = len(datasets)
client_weights = [1/client_num for i in range(client_num)]
# each local client model
models = [copy.deepcopy(server_model).to(device) for idx in range(client_num)]

best_epoch = 0
best_f1 = [0. for j in range(client_num)] 
start_iter = 0

result_train_loss = {}
result_train_sec_acc = {}
result_train_win_acc = {}
result_train_f1 = {}
result_train_recall = {}
result_train_precision = {}

result_test_sec_acc = {}
result_test_win_acc = {}
result_test_f1 = {}
result_test_recall = {}
result_test_precision = {}

for i in range(args.client_num):    
    result_train_loss[i] = []
    result_train_sec_acc[i] = []
    result_train_win_acc[i] = []
    result_train_f1[i] = []
    result_train_recall[i] = []
    result_train_precision[i] = []

    result_test_sec_acc[i] = []
    result_test_win_acc[i] = []
    result_test_f1[i] = []
    result_test_recall[i] = []
    result_test_precision[i] = []

# Start training
for a_iter in range(start_iter, args.iters):
#     optimizers = [optim.SGD(params = models[idx].parameters(), lr=args.lr, momentum = args.client_momentum) for idx in range(client_num)]
    for wi in range(args.wk_iters):
        print("============ Train epoch {} ============".format(wi + a_iter * args.wk_iters))
        for client_idx, model in enumerate(models):
            print('Client ', client_idx)
            trainer = Trainer(model, options, args.client_num, client_idx)
            trainer.start_train()
            
#             train_loss = train(model, train_loaders[client_idx], optimizers[client_idx], device, args.local_epoches)
#             result_train_loss[client_idx].append(train_loss)
    with torch.no_grad():
        # aggregation
        server_model, models, v, grad = communication(args, server_model, models, client_weights, v, grad )
        # Report loss after aggregation

#         for client_idx, model in enumerate(models):
#             tr_metrics = test(model, train_loaders[client_idx], device)
#             result_train_sec_acc[client_idx].append(tr_metrics['session_acc'])
#             result_train_win_acc[client_idx].append(tr_metrics['window_acc'])
#             result_train_f1[client_idx].append(tr_metrics['f1'])
#             result_train_recall[client_idx].append(tr_metrics['recall'])
#             result_train_precision[client_idx].append(tr_metrics['precision'])
            
#             print(' {:<8s}| Loss: {:.4f} | Session Acc: {:.4f}| Window Acc: {:.4f} | F1: {:.4f} | Recall: {:.4f} | Precision: {:.4f} '.format(datasets[client_idx], result_train_loss[client_idx][-1], result_train_sec_acc[client_idx][-1], result_train_win_acc[client_idx][-1],
#                                                                                 result_train_f1[client_idx][-1], result_train_recall[client_idx][-1], result_train_precision[client_idx][-1])) 
          
        print("============ Test epoch {} ============".format(wi + a_iter * args.wk_iters))
#         # Validation
#         val_f1_list = [None for j in range(client_num)]
        for client_idx, model in enumerate(models):
            print('Client ', client_idx)
            predicter = Predicter(model, options, args.client_num, client_idx)
            predicter.predict_unsupervised()
#             te_metrics = test(model, test_loaders[client_idx], device)
#             val_f1_list[client_idx] = te_metrics['f1']
#             result_test_sec_acc[client_idx].append(te_metrics['session_acc'])
#             result_test_win_acc[client_idx].append(te_metrics['window_acc'])
#             result_test_f1[client_idx].append(te_metrics['f1'])
#             result_test_recall[client_idx].append(te_metrics['recall'])
#             result_test_precision[client_idx].append(te_metrics['precision'])
            
#             print(' {:<8s}| Session Acc: {:.4f}| Window Acc: {:.4f} | F1: {:.4f} | Recall: {:.4f} | Precision: {:.4f} '.format(datasets[client_idx], result_test_sec_acc[client_idx][-1], result_test_win_acc[client_idx][-1],
#                                                                                 result_test_f1[client_idx][-1], result_test_recall[client_idx][-1], result_test_precision[client_idx][-1])) 
            
#         # Record best
#         if np.mean(val_f1_list) > np.mean(best_f1):
#             for client_idx in range(client_num):
#                 best_f1[client_idx] = val_f1_list[client_idx]
#                 best_epoch = a_iter
#                 best_changed=True

# for client_idx in range(client_num):
#     print(' Best {:<10s}| Epoch:{} |Test F1: {:.4f}'.format(datasets[client_idx], best_epoch, best_f1[client_idx]))

============ Train epoch 0 ============
Client  0
File ../data/hdfs/hdfs_train, number of sessions 971
File ../data/hdfs/hdfs_train, number of seqs 9420
sampling...


100%|██████████| 1058/1058 [00:00<00:00, 3587.82it/s]


File ../data/hdfs/hdfs_test_normal, number of sessions 110673
File ../data/hdfs/hdfs_test_normal, number of seqs 1058
Find 9420 train logs, 1058 validation logs
Train batch size 2048 ,Validation batch size 2048
Starting epoch: 0 | phase: train | ⏰: 17:05:09 | Learning rate: 0.000031


Train loss: 3.31278: 100%|██████████| 5/5 [00:00<00:00, 52.79it/s]


Starting epoch: 0 | phase: valid | ⏰: 17:05:09 


...

false positive (FP): 467, false negative (FN): 30, Precision: 87.723%, Recall: 99.109%, F1-measure: 93.069%
Finished Predicting
elapsed_time: 201.85426950454712
Client  3
Number of sessions(hdfs_test_normal): 5747
Number of sessions(hdfs_test_abnormal): 1159


100%|██████████| 1159/1159 [00:15<00:00, 76.05it/s]


false positive (FP): 447, false negative (FN): 28, Precision: 88.193%, Recall: 99.168%, F1-measure: 93.359%
Finished Predicting
elapsed_time: 140.81818342208862
Client  4
Number of sessions(hdfs_test_normal): 5623
Number of sessions(hdfs_test_abnormal): 1121


100%|██████████| 1121/1121 [00:19<00:00, 57.97it/s]

false positive (FP): 521, false negative (FN): 33, Precision: 86.485%, Recall: 99.020%, F1-measure: 92.329%
Finished Predicting
elapsed_time: 196.6334457397461


In [12]:
# # test on global model
# if args.mode.lower() == 'fedbn':
#     pass
# else:
#     for client_idx in range(client_num):
#         models[client_idx].load_state_dict(server_model.state_dict())
        
# for test_idx, test_loader in enumerate(test_loaders):
#     metrics = test(server_model, test_loader, device)
#     print(' {:<8s}| Session Acc: {:.4f}| Window Acc: {:.4f} | F1: {:.4f} | Recall: {:.4f} | Precision: {:.4f} '.format(datasets[test_idx], metrics['session_acc'], metrics['window_acc'], metrics['f1'], metrics['recall'], metrics['precision']))

predicter = Predicter(server_model.to(device), options, 1, 0)
predicter.predict_unsupervised()

Number of sessions(hdfs_test_normal): 14177
Number of sessions(hdfs_test_abnormal): 4123


100%|██████████| 4123/4123 [01:23<00:00, 49.50it/s]

false positive (FP): 2442, false negative (FN): 140, Precision: 87.241%, Recall: 99.169%, F1-measure: 92.823%
Finished Predicting
elapsed_time: 523.0870118141174


In [13]:
# (pd.DataFrame.from_dict(data=result_train_loss, orient='index').to_csv('../data/result_all/Fedavg_232_1_train_loss.csv', header=False))

# (pd.DataFrame.from_dict(data=result_train_sec_acc, orient='index').to_csv('../data/result_all/Fedavg_232_1_train_sec_acc.csv', header=False))
# (pd.DataFrame.from_dict(data=result_train_win_acc, orient='index').to_csv('../data/result_all/Fedavg_232_1_train_win_acc.csv', header=False))
# (pd.DataFrame.from_dict(data=result_train_f1, orient='index').to_csv('../data/result_all/Fedavg_232_1_train_f1.csv', header=False))
# (pd.DataFrame.from_dict(data=result_train_recall, orient='index').to_csv('../data/result_all/Fedavg_232_1_train_recall.csv', header=False))
# (pd.DataFrame.from_dict(data=result_train_precision, orient='index').to_csv('../data/result_all/Fedavg_232_1_train_precision.csv', header=False))

# (pd.DataFrame.from_dict(data=result_test_sec_acc, orient='index').to_csv('../data/result_all/Fedavg_232_1_test_sec_acc.csv', header=False))
# (pd.DataFrame.from_dict(data=result_test_win_acc, orient='index').to_csv('../data/result_all/Fedavg_232_1_test_win_acc.csv', header=False))
# (pd.DataFrame.from_dict(data=result_test_f1, orient='index').to_csv('../data/result_all/Fedavg_232_1_test_f1.csv', header=False))
# (pd.DataFrame.from_dict(data=result_test_recall, orient='index').to_csv('../data/result_all/Fedavg_232_1_test_recall.csv', header=False))
# (pd.DataFrame.from_dict(data=result_test_precision, orient='index').to_csv('../data/result_all/Fedavg_232_1_test_precision.csv', header=False))

In [14]:
# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_train_loss[i], label = datasets[i])
# plt.title('Loss')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_train_sec_acc[i], label = datasets[i])
# plt.title('Session Acc')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_train_win_acc[i], label = datasets[i])
# plt.title('Window Acc')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_train_f1[i], label = datasets[i])
# plt.title('F1 Score')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_train_recall[i], label = datasets[i])
# plt.title('Recall')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_train_precision[i], label = datasets[i])
# plt.title('Precison')
# plt.legend()
# plt.show()

In [15]:
# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_test_sec_acc[i], label = datasets[i])
# plt.title('Session Acc')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_test_win_acc[i], label = datasets[i])
# plt.title('Window Acc')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_test_f1[i], label = datasets[i])
# plt.title('F1 Score')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_test_recall[i], label = datasets[i])
# plt.title('Recall')
# plt.legend()
# plt.show()

# for i in range(client_num):
#     plt.plot(np.arange(args.iters), result_test_precision[i], label = datasets[i])
# plt.title('Precison')
# plt.legend()
# plt.show()

In [16]:
# result_record_train = pd.DataFrame.from_dict(data=result_train_f1, orient='index')
# result_record_train = np.mean(np.array(result_record_train), axis = 0)
# result_record_train = result_record_train.reshape(-1)

# result_record_test = pd.DataFrame.from_dict(data=result_test_f1, orient='index')
# result_record_test = np.mean(np.array(result_record_test), axis = 0)
# result_record_test = result_record_test.reshape(-1)

# plt.plot(np.arange(args.iters), result_record_train, label = 'Train')
# plt.plot(np.arange(args.iters), result_record_test, label = 'Test')
# plt.title('Average F1 score')
# plt.legend()
# plt.show()

In [17]:
# result_record_train_loss = pd.DataFrame.from_dict(data=result_train_loss, orient='index')
# result_record_train_loss = np.mean(np.array(result_record_train_loss), axis = 0)
# result_record_train_loss = result_record_train_loss.reshape(-1)


# plt.plot(np.arange(args.iters), result_record_train_loss, label = 'Train')
# plt.title('Average train loss')
# plt.legend()
# plt.show()